In [41]:
from qiskit import QuantumCircuit
from qiskit_aer import AerSimulator

from typing import List

In [42]:
R = 8  # Rate
B = 88  # State width
N = 88  # Hash size
ROUNDS = 45  # Number of rounds in the Pi permutation
INITIAL_LFSR_STATE = "000101"
LFSR_TAPS = [4, 5]
SBOX_WIDTH = 4

Mapping = List[int]

In [43]:
def lfsr_state(
    round: int, initial_state: str = INITIAL_LFSR_STATE, taps: list = LFSR_TAPS
):
    state = list(map(int, initial_state))

    for _ in range(round):
        feedback_bit = 0
        for tap in taps:
            feedback_bit ^= state[len(initial_state) - 1 - tap]

        state = state[1:] + [feedback_bit]

    return "".join(map(str, state))

In [44]:
def l_counter_gate_factory(round: int):
    state = lfsr_state(round)

    l_counter = QuantumCircuit(B)

    for bit, i in enumerate(state[::-1]):
        if i == "1":
            l_counter.x(bit)
            l_counter.x(B - 1 - bit)

    return l_counter.to_gate(label="lcounter")

In [45]:
def sbox_gate_factory():
    sbox = QuantumCircuit(SBOX_WIDTH)

    sbox.x(1)
    sbox.ccx(2, 1, 0)
    sbox.cx(1, 2)
    sbox.cx(3, 0)
    sbox.cx(0, 1)
    sbox.x(0)
    sbox.ccx(3, 2, 1)
    sbox.ccx(1, 0, 3)
    sbox.x(1)
    sbox.cx(2, 0)
    sbox.ccx(3, 1, 2)
    sbox.cx(2, 1)
    sbox.cx(0, 3)

    return sbox.to_gate(label="sbox")

In [46]:
def sbox_layer_gate_factory():
    sbox_layer = QuantumCircuit(B)

    for i in range(0, B, SBOX_WIDTH):
        sbox_layer.append(sbox_gate_factory(), list(range(i, i + SBOX_WIDTH)))

    return sbox_layer.to_gate(label="sbox_layer")

In [47]:
def get_permuted_index(index: int):
    assert 0 <= index < B

    if 0 <= index <= B - 2:
        return int((index * B / 4) % (B - 1))
    else:
        return index

In [48]:
def get_permutation(mapping: Mapping):
    new_mapping = [None] * B
    for i, j in enumerate(mapping):
        new_mapping[get_permuted_index(j)] = i
    reverse_mapping = [get_permuted_index(i) for i in mapping]
    return new_mapping, reverse_mapping

In [49]:
def pi_permutation_gate(gate_mapping: Mapping, register_mapping: Mapping):
    pi_permutation = QuantumCircuit(B)

    for round_number in range(ROUNDS):
        l_counter_gate = l_counter_gate_factory(round_number)
        sbox_layer_gate = sbox_layer_gate_factory()

        pi_permutation.append(l_counter_gate, gate_mapping)
        pi_permutation.append(sbox_layer_gate, gate_mapping)
        gate_mapping, register_mapping = get_permutation(register_mapping)

    return pi_permutation.to_gate(label="pi_permutation"), gate_mapping, register_mapping

In [50]:
def absorb_phase_gate_factory(message_size: int):
    excess_bits = message_size % R
    padding_size = R - excess_bits

    absorb_phase = QuantumCircuit(
        B + max(message_size - R, 0)
    )  # The first 8 bits of the message are fed directly into the first 8 bits of the state

    gate_mapping = list(range(B))
    register_mapping = list(range(B))

    i = 0
    for i in range(0, max(message_size - R, 0) - excess_bits, R):
        pi_permutation, gate_mapping, register_mapping = pi_permutation_gate(
            gate_mapping, register_mapping
        )
        absorb_phase.append(pi_permutation, list(range(B)))

        for j, k in enumerate(range(i, i + R)):
            absorb_phase.cx(B + k, gate_mapping[j])

    if message_size >= 8:
        pi_permutation, gate_mapping, register_mapping = pi_permutation_gate(
            gate_mapping, register_mapping
        )
        absorb_phase.append(pi_permutation, list(range(B)))

    i += R
    for n, m in enumerate(range(i, i + excess_bits)):
        absorb_phase.cx(B + m, gate_mapping[padding_size + n])
    absorb_phase.x(gate_mapping[padding_size - 1])

    pi_permutation, gate_mapping, register_mapping = pi_permutation_gate(
        gate_mapping, register_mapping
    )
    absorb_phase.append(pi_permutation, list(range(B)))

    return absorb_phase.to_gate(label="absorb_phase"), gate_mapping, register_mapping


In [51]:
def squeeze_phase_gate_factory(
    message_size: int, gate_mapping: Mapping, register_mapping: Mapping
):
    squeeze_phase = QuantumCircuit(B + max(message_size - R, 0) + N)

    for i in range(0, N, R):
        for j in range(R):
            squeeze_phase.cx(gate_mapping[j], squeeze_phase.width() - R - i + j)

        if i < B - R:  # Don't add a permutation gate at the end.
            pi_permutation, gate_mapping, register_mapping = pi_permutation_gate(
                gate_mapping, register_mapping
            )
            squeeze_phase.append(pi_permutation, list(range(B)))

    return squeeze_phase.to_gate(label="squeeze_phase"), gate_mapping, register_mapping

In [52]:
def reversible_spongent_gate_factory(message_size: int):
    spongent = QuantumCircuit(B + max(message_size - R, 0) + N)

    absorb_gate, gate_mapping, register_mapping = absorb_phase_gate_factory(
        message_size
    )
    squeeze_gate, _, register_mapping = squeeze_phase_gate_factory(
        message_size, gate_mapping, register_mapping
    )

    spongent.append(absorb_gate, list(range(spongent.width() - N)))
    spongent.append(squeeze_gate, list(range(spongent.width())))

    return spongent.to_gate(label="spongent"), register_mapping

In [53]:
def spongent_circuit(message_size: int):
    circuit_width = B + max(message_size - R, 0) + N
    spongent_circuit = QuantumCircuit(circuit_width)
    spongent_gate, register_mapping = reversible_spongent_gate_factory(message_size)
    spongent_circuit.append(spongent_gate, list(range(circuit_width)))

    return spongent_circuit, register_mapping

In [54]:
spongent_circuit, register_mapping = spongent_circuit(32)

In [58]:
spongent_circuit.decompose(reps=2).draw("mpl")